In [1]:
%matplotlib inline
from matplotlib import pyplot as plt
import pandas as pd
import numpy as np
import datetime
import math
import random
import os

In [2]:
file_path = "./normal.csv"
df = pd.read_csv(file_path)
norvalue = df['value'].values

file_path = "./traindata.csv"
df = pd.read_csv(file_path)
convalue = df['value'].values

In [3]:
import torch 
import torch.nn as nn
from torch.autograd import Variable 
import torch.nn.functional as F 

class Network(nn.Module):
    def __init__(self):
        super().__init__()

        self.hidden = nn.Linear(2, 10)
        self.output = nn.Linear(10, 3)

        self.sigmoid = nn.Sigmoid()
        self.softmax = nn.Softmax(dim=1)
        self.relu = nn.ReLU(inplace=False)


    def forward(self, x):
        x = self.hidden(x)
        x = torch.tanh(x)
        x = self.output(x)
        return x
    

Or_Data = np.concatenate([norvalue.reshape(-1,1),convalue.reshape(-1,1)],axis=1)
Data = Variable(torch.from_numpy(Or_Data),requires_grad=True).to(torch.float32)

net = Network()
optimizer=torch.optim.SGD(net.parameters(), lr=0.000001)
loss_func=nn.L1Loss()
y = torch.from_numpy(norvalue).float()
x = torch.from_numpy(convalue).float()
data = torch.from_numpy(Or_Data).float()

E:\anaconda3\envs\torch\lib\site-packages\tqdm\auto.py:22: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [37]:
# class Pid():
#     def __init__(self, exp_val, con_val, kp, ki, kd):
#         self.KP = kp
#         self.KI = ki
#         self.KD = kd
#         self.exp_val = exp_val
#         self.now_val = con_val
#         self.sum_err = 0
#         self.now_err = 0
#         self.last_err = 0

#     def cmd_pid(self):
#         self.last_err = self.now_err
#         self.now_err = self.exp_val - self.now_val
#         self.sum_err += self.now_err
#         # 这一块是严格按照公式来写的
#         self.now_val = self.KP * (self.exp_val - self.now_val) \
#                         + self.KI * self.sum_err + self.KD * (self.now_err - self.last_err)
#         return self.now_val
    
def pid_soa(kpidi):
    lastvalue = []   #存储最后pid迭代的值
    for j in range(0,len(convalue)):   #一次控制2501个数据(即0.2s)，共用一个pid控制器
        erro = norvalue[j]-convalue[j]
        a = (outputs[0]*erro + outputs[1]*erro+outputs[2]*erro)
        erro1 = y[batch]-a
        b = (outputs[0]*erro1 + outputs[1]*(erro+erro1)+outputs[2]*(erro1-erro))
        
        lastvalue.append(b)
                
    return np.linalg.norm(norvalue-lastvalue)

In [26]:
new = torch.Tensor([0])
losslist = []
batch = 0
parameter = []
edu = []
for batch in range(len(convalue)):
    setv = 2
    
    while setv>1.5:
        outputs=net(data[batch])

        erro = y[batch]-x[batch]
        a = (outputs[0]*erro + outputs[1]*erro+outputs[2]*erro)
        erro1 = y[batch]-a
        b = (outputs[0]*erro1 + outputs[1]*(erro+erro1)+outputs[2]*(erro1-erro))

        loss=loss_func(b,y[batch])
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        setv = float(loss)

    
    losslist.append(setv)
    outputs = outputs.detach().numpy()
    parameter.append(outputs)    
    print(setv, outputs)

        
            


0.04528379440307617 [ 0.07445458  1.0552106  -0.03861335]
0.0028533935546875 [ 0.06325755  1.0503471  -0.03561962]
0.05790543556213379 [ 0.06158704  1.0230283  -0.04076892]
0.00461423397064209 [ 0.13347611  0.9522376  -0.06352131]
0.12259680032730103 [ 0.41183913  0.84834254 -0.16061409]
0.05343365669250488 [ 0.6515931   0.6169227  -0.33419466]
0.07754373550415039 [ 0.69526553  0.45357478 -0.3783013 ]
0.0261993408203125 [ 0.72109735  0.38520813 -0.401203  ]
0.026718616485595703 [ 0.76685613  0.37324345 -0.42743   ]
0.016277790069580078 [ 0.817865    0.4062498  -0.44614807]
0.002273082733154297 [ 0.8131162   0.53531855 -0.41488808]
0.024254977703094482 [ 0.5885296   0.82347643 -0.25143182]
0.02200603485107422 [ 0.2042762   0.9332216  -0.11075509]
0.029102087020874023 [ 0.03461     1.0381832  -0.02189092]
0.10764169692993164 [-0.02711558  1.0925198   0.02897016]
0.18244409561157227 [-0.05861597  1.1099098   0.05503225]
0.13425540924072266 [-0.06393664  1.1028178   0.05526319]
0.027345418

0.07626676559448242 [ 0.10400753  1.0161753  -0.06405184]
0.05792522430419922 [ 0.08597649  1.051483   -0.04439162]
0.13974666595458984 [ 0.06298558  1.0696429  -0.0258441 ]
0.10914373397827148 [ 0.03054453  1.0779264  -0.00759055]
0.01914501190185547 [-0.00315072  1.0624344   0.00634641]
0.03549325466156006 [0.0287056  0.973733   0.00809366]
0.14911597967147827 [ 0.35738492  0.84320945 -0.1363944 ]
0.07923388481140137 [ 0.660769   0.5920528 -0.3433248]
0.0335392951965332 [ 0.7590082   0.41357362 -0.4159096 ]
0.04773378372192383 [ 0.8359623   0.34957087 -0.4689853 ]
0.06849098205566406 [ 0.90214366  0.33922076 -0.5056244 ]
0.049199581146240234 [ 0.9335561   0.37634498 -0.5129145 ]
0.007271528244018555 [ 0.86573917  0.5493881  -0.436372  ]
0.05233044922351837 [ 0.49914718  0.8665532  -0.21185777]
0.02290940284729004 [ 0.02369232  0.99570537 -0.00113759]
0.1562204360961914 [-0.16249599  1.0981472   0.12764472]
0.2961263656616211 [-0.24409346  1.1302475   0.1907448 ]
0.33295679092407227 [

0.10683393478393555 [ 0.65843546  0.37775397 -0.36884645]
0.09084033966064453 [ 0.67987496  0.37458667 -0.38110474]
0.04477405548095703 [ 0.7238447   0.4245736  -0.39647257]
0.02152419090270996 [ 0.7252131   0.58016086 -0.3693672 ]
0.008760243654251099 [ 0.44664598  0.8714459  -0.18184997]
0.0697011947631836 [ 0.12550658  0.9706532  -0.07833989]
0.005033969879150391 [ 0.05838633  1.0524769  -0.03206193]
0.18602514266967773 [ 0.05220845  1.0781398  -0.01673085]
0.2622990608215332 [ 0.04873228  1.0844991  -0.01072245]
0.18917417526245117 [ 0.04037905  1.0830379  -0.00917987]
0.02236318588256836 [ 0.03159662  1.0640155  -0.01493447]
0.023200035095214844 [ 0.07405825  0.9892785  -0.04246974]
0.08585965633392334 [ 0.36091292  0.8726208  -0.13419136]
0.04361224174499512 [ 0.66064787  0.6148009  -0.33754402]
0.06347036361694336 [ 0.7017838   0.44364122 -0.3823303 ]
0.05242204666137695 [ 0.72018695  0.37595218 -0.4019385 ]
0.05629158020019531 [ 0.75839615  0.36284867 -0.42488995]
0.00061368942

0.00043523311614990234 [ 0.12788089  0.9561645  -0.06315994]
0.07469388097524643 [ 0.24349698  0.889802   -0.07417457]
0.07739043235778809 [ 0.495926   0.7592245 -0.2339455]
0.14054656028747559 [ 0.6088337   0.58419126 -0.32286257]
0.07380390167236328 [ 0.6505377   0.45480776 -0.3555326 ]
0.0073108673095703125 [ 0.70065194  0.4005442  -0.3876866 ]
0.022458553314208984 [ 0.761867    0.407176   -0.41790286]
0.028359413146972656 [ 0.80159354  0.4901548  -0.42071816]
0.022919774055480957 [ 0.67100525  0.7536406  -0.29750314]
0.003180384635925293 [ 0.306275    0.90161526 -0.15935236]
0.11468863487243652 [ 0.11376785  0.9930198  -0.07435709]
0.024013519287109375 [ 0.06916583  1.0535913  -0.03693604]
0.1473560333251953 [ 0.04179482  1.0790575  -0.01243393]
0.15359926223754883 [0.01600346 1.0884651  0.00421962]
0.0579991340637207 [-0.00272055  1.0788791   0.00921971]
0.0002148151397705078 [ 0.00995913  1.0277159  -0.00262014]
0.004494667053222656 [ 0.16738814  0.92336035 -0.05382074]
0.1213557

0.08468788862228394 [-0.11106977  0.86946154  0.14133652]
0.12341701984405518 [-0.2994435   1.0038228   0.26651204]
0.1912219524383545 [-0.22374743  1.0930588   0.17705363]
0.15225696563720703 [-0.10848203  1.109307    0.08685379]
0.035457611083984375 [ 0.01500516  1.0710031  -0.00379074]
0.14725685119628906 [ 0.13833018  0.97447497 -0.08931252]
0.10395216941833496 [ 0.32442653  0.83389044 -0.17546065]
0.3106945753097534 [ 0.6217373  0.817127  -0.2875018]
0.1332036256790161 [ 0.80632204  0.7079092  -0.377101  ]
0.011685848236083984 [ 0.83604807  0.5351426  -0.42428142]
0.06493878364562988 [ 0.74270624  0.4992802  -0.39273915]
0.13427090644836426 [ 0.6307536   0.53473943 -0.3374845 ]
0.15428829193115234 [ 0.5700746  0.6059966 -0.3023401]
0.022742509841918945 [ 0.5394328   0.70275724 -0.27119592]
0.1497572660446167 [ 0.4082393   0.8304677  -0.16382599]
0.01574718952178955 [ 0.25066283  0.91620874 -0.10400553]
0.07902562618255615 [ 0.17974317  0.94131863 -0.10843723]
0.14876794815063477 [

...

0.32393527030944824 [ 0.8103714  0.755761  -0.3799216]
0.14422321319580078 [ 0.99641395  0.60049844 -0.51986206]
0.016051769256591797 [ 1.0556998   0.50760674 -0.5769232 ]
0.0027146339416503906 [ 1.004823    0.474688   -0.53634316]
0.010116338729858398 [ 0.8433888   0.5544633  -0.42343506]
0.08330166339874268 [ 0.5229814   0.7750254  -0.24808669]
0.09962058067321777 [0.06357192 0.8606801  0.01302629]
0.09256821870803833 [-0.2613446   0.91677177  0.24668302]
0.057729363441467285 [-0.30273008  1.0108232   0.27025414]
0.09378814697265625 [-0.16634217  1.0739217   0.13894959]
0.014483451843261719 [0.00116716 1.0639535  0.00764743]
0.05678844451904297 [ 0.15259787  0.9877002  -0.09004964]
0.011323809623718262 [ 0.31787676  0.89371777 -0.16829082]
0.2101980447769165 [ 0.52637947  0.8607327  -0.24812657]
0.1992950439453125 [ 0.6815007   0.8206101  -0.30639017]
0.015726804733276367 [ 0.7406203   0.70929265 -0.34179127]
0.024108171463012695 [ 0.7202197  0.639927  -0.3544539]
0.03030896186828613

0.13879406452178955 [ 0.30107304  0.85600257 -0.12031194]
0.06983041763305664 [ 0.48843098  0.74467486 -0.25302622]
0.15675640106201172 [ 0.60137135  0.5934849  -0.32002383]
0.06752824783325195 [ 0.7166322   0.477452   -0.38246652]
0.00018167495727539062 [ 0.8428006   0.42881805 -0.44911402]
0.020315885543823242 [ 0.9384996   0.4502239  -0.49432558]
0.09884250164031982 [ 0.9098568   0.6225649  -0.44974658]
0.33330386877059937 [ 0.65008616  0.83164865 -0.29884782]
0.06985211372375488 [ 0.23540774  0.9277457  -0.13264899]
0.0583653450012207 [ 0.0553914   1.0828887  -0.02529048]
0.24768924713134766 [-0.06998824  1.1479102   0.0670912 ]
0.2943406105041504 [-0.17496961  1.1678798   0.13813204]
0.2326674461364746 [-0.23283666  1.1576481   0.17402884]
0.13741755485534668 [-0.21693966  1.1105859   0.16855346]
0.008461952209472656 [-0.01391724  0.97519815  0.05927816]
0.08263850212097168 [ 0.6291727  0.7662924 -0.2825409]
0.03125739097595215 [ 0.9447484  0.4258639 -0.5021535]
0.1508154869079589

0.053090572357177734 [-0.07402258  1.0758997   0.06405783]
0.11611366271972656 [-0.04726712  1.125289    0.04425105]
0.20680952072143555 [0.01546706 1.1196532  0.00888034]
0.18238401412963867 [ 0.07081577  1.0949359  -0.02769362]
0.0461726188659668 [ 0.11698031  1.0531708  -0.06306215]
0.08350753784179688 [ 0.1771917   0.9739168  -0.10376676]
0.027357935905456543 [ 0.35044432  0.8937254  -0.1807055 ]
0.07655024528503418 [ 0.6308586  0.827976  -0.2763722]
0.0025517940521240234 [ 0.7554133   0.5935341  -0.37885883]
0.07839393615722656 [ 0.70075244  0.49256983 -0.37289768]
0.04413414001464844 [ 0.63425565  0.46303123 -0.3429653 ]
0.0688176155090332 [ 0.6164049   0.4795382  -0.33288378]
0.12623214721679688 [ 0.64064896  0.54881376 -0.34016415]
0.024958133697509766 [ 0.6238386   0.69745857 -0.30749747]
0.035988032817840576 [ 0.41767907  0.89275825 -0.1678581 ]
0.012479424476623535 [ 0.20677625  0.9577699  -0.1107655 ]
0.06118345260620117 [ 0.13116059  1.0104465  -0.07884175]
0.0106759071350

0.007002592086791992 [ 0.83175635  0.53907967 -0.42127603]
0.01282048225402832 [ 0.8987345   0.47595805 -0.46661183]
0.01053476333618164 [ 0.9031787   0.49590474 -0.4651182 ]
0.009838104248046875 [ 0.8262509   0.61089295 -0.40209317]
0.03147709369659424 [ 0.59226775  0.8214598  -0.2553056 ]
0.01618868112564087 [ 0.19079073  0.93838215 -0.06006651]
0.051613688468933105 [-0.09953371  1.0214005   0.10340019]
0.11148571968078613 [-0.20953767  1.0761006   0.17214197]
0.11487770080566406 [-0.19653907  1.095444    0.15558062]
0.0561983585357666 [-0.08629765  1.0794338   0.07190419]
0.01755845546722412 [ 0.11708879  0.99728096 -0.06328024]
0.14287209510803223 [ 0.4674413   0.87987375 -0.22448963]
0.3460930287837982 [ 0.7972232   0.76590633 -0.37293762]
0.15489816665649414 [ 0.95356023  0.6217079  -0.48320943]
0.03005838394165039 [ 0.9980459   0.51831526 -0.52596307]
0.005769252777099609 [ 0.93607974  0.49531016 -0.48447493]
0.00943446159362793 [ 0.75818515  0.5977333  -0.37839708]
0.0467797517

0.06841230392456055 [ 0.25676638  0.91430503 -0.14336191]
0.000668644905090332 [ 0.29094893  0.92184514 -0.15408076]
0.04918143153190613 [ 0.3627946   0.9194201  -0.16004986]
0.10901784896850586 [ 0.46306056  0.8576695  -0.18983898]
0.07684588432312012 [ 0.54756355  0.76166177 -0.26098177]
0.0395505428314209 [ 0.5740763   0.7006533  -0.29249555]
0.06685900688171387 [ 0.5803462   0.68383193 -0.29877996]
0.0008559226989746094 [ 0.5807836   0.71289945 -0.29046628]
0.12044429779052734 [ 0.5315238   0.79554355 -0.23930289]
0.03892558813095093 [ 0.40608016  0.8950864  -0.16229823]
0.03220444917678833 [ 0.28478253  0.93547326 -0.13680464]
0.04341161251068115 [ 0.21720679  0.9498298  -0.12239783]
0.07750988006591797 [ 0.19009528  0.96188146 -0.11155754]
0.07915735244750977 [ 0.17989446  0.96957123 -0.10628423]
0.0610051155090332 [ 0.17627612  0.9722724  -0.10321905]
0.005109548568725586 [ 0.19051942  0.9639176  -0.0994076 ]
0.00872763991355896 [ 0.24333075  0.93274736 -0.08940157]
0.1505861282

In [29]:
losslist.index(min(losslist))

38090

In [41]:
import time
start = time.time()
for i in range(1):
    edu = pid_soa(parameter[i])
end = time.time()

In [42]:
end - start

4.806139945983887